In [1]:
query = "attendance policy"

In [ ]:
from langchain_community.document_loaders import JSONLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_community.embeddings import GPT4AllEmbeddings
from langchain_community.vectorstores import Chroma

In [19]:
import json
from pathlib import Path
from pprint import pprint

In [20]:
file_path='../data/test.json'

In [21]:
json_data = json.loads(Path(file_path).read_text())

In [22]:
print(len(json_data['docs']))

4265


In [23]:
from gpt4all import Embed4All
import numpy as np

In [24]:
# Initialize Embed4All
embeddings = Embed4All()
query_vec = embeddings.embed(query)

In [25]:
secondary_data = json.load(open('../data/secondary_data.json'))
print(secondary_data)

{'Judson-MATH-1A-01-W19': {'grading policy | marks distribution': 'Grade\nYour grade will be computed using the following grade distribution.\n5% Labs 10% Quizzes. 8 Ch. 4.4\n\nQuiz 9\nHw 13 due\n22 Lab 6due\n\n \n\x0cLab Grading Policies. will be graded out of 5 points each. You will not know which 4 problems will be graded. For the. Grading Scale\n\nDue to the complexity of the material the grading scale we will use is as follows. General Grading: Each lab member is required to turn in their own lab report. Failure to turn in a. '}, 'Lien-MATH-1A-05-W19': {'grading policy | marks distribution': 'Final grades are non-negotiable. You should monitor your scores in the gradebook regularly. QUESTION: What is my current grade in the class?. Breakdown of grades:\nHomework\n63-879% «BO\n\n80-82.9% «|B\n63-679% «(DS\n60-62.9% «(| D-. marks incorrectly. Problems must be brought to my attention immediately after exams are returned.. - You are required to come to class prepared WITH lecture note

In [26]:
secondary_data

{'Judson-MATH-1A-01-W19': {'grading policy | marks distribution': 'Grade\nYour grade will be computed using the following grade distribution.\n5% Labs 10% Quizzes. 8 Ch. 4.4\n\nQuiz 9\nHw 13 due\n22 Lab 6due\n\n \n\x0cLab Grading Policies. will be graded out of 5 points each. You will not know which 4 problems will be graded. For the. Grading Scale\n\nDue to the complexity of the material the grading scale we will use is as follows. General Grading: Each lab member is required to turn in their own lab report. Failure to turn in a. '},
 'Lien-MATH-1A-05-W19': {'grading policy | marks distribution': 'Final grades are non-negotiable. You should monitor your scores in the gradebook regularly. QUESTION: What is my current grade in the class?. Breakdown of grades:\nHomework\n63-879% «BO\n\n80-82.9% «|B\n63-679% «(DS\n60-62.9% «(| D-. marks incorrectly. Problems must be brought to my attention immediately after exams are returned.. - You are required to come to class prepared WITH lecture not

In [27]:
from gpt4all import Embed4All
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity

# Initialize Embed4All
embeddings = Embed4All()

# # Define the query string
# query = "your query string"

# # Embed the query
# query_vec = embeddings.embed(query)

# Iterate over each document
# for doc_id in range(len(json_data['docs'])):
for doc_id in range(500):
    doc_str = json_data['docs'][doc_id]['content']

    text_splitter = RecursiveCharacterTextSplitter(chunk_size=100, chunk_overlap=10)
    doc_split = text_splitter.create_documents([doc_str])

    # Embed the documents
    doc_vecs = np.array([embeddings.embed(sub_doc.page_content) for sub_doc in doc_split])

    # Compute cosine similarity scores
    scores = cosine_similarity([query_vec], doc_vecs)[0]

    # Get top k documents
    k = 5
    top_docs_indices = np.argsort(-scores)[:k]
    top_docs = [doc_split[i] for i in top_docs_indices]

    # print("title:", json_data['docs'][doc_id]['title'])
    # print("matching substrings:")
    final_doc_str = ""
    for sub_doc in top_docs:
        # print(sub_doc.page_content)
        final_doc_str += sub_doc.page_content + ". "
    
    if json_data['docs'][doc_id]['title'] not in secondary_data:
        secondary_data[json_data['docs'][doc_id]['title']] = {}
    secondary_data[json_data['docs'][doc_id]['title']][query] = final_doc_str    
    # secondary_data[json_data['docs'][doc_id]['title']]['retrieved_content'] = final_doc_str

    if doc_id %10 == 0:
        print(doc_id)
    # print("\n")

0
10
20
30
40
50
60
70
80
90
100
110
120
130
140
150
160
170
180
190
200
210
220
230
240
250
260
270
280
290
300
310
320
330
340
350
360
370
380
390
400
410
420
430
440
450
460
470
480
490


In [28]:
secondary_data

{'Judson-MATH-1A-01-W19': {'grading policy | marks distribution': 'Grade\nYour grade will be computed using the following grade distribution.\n5% Labs 10% Quizzes. 8 Ch. 4.4\n\nQuiz 9\nHw 13 due\n22 Lab 6due\n\n \n\x0cLab Grading Policies. will be graded out of 5 points each. You will not know which 4 problems will be graded. For the. Grading Scale\n\nDue to the complexity of the material the grading scale we will use is as follows. General Grading: Each lab member is required to turn in their own lab report. Failure to turn in a. ',
  'attendance policy': 'Accomodations\n\nHonors. Those of you who need additional accommodations, due to disability, campus-related. may, of course, make arrangements with other members of the class to declare yourself as part of. course you are not required to do the Honors Problems. No late work will be accepted. Your. Incompletes: To avoid groups being penalized for a member who does not complete certain sections. '},
 'Lien-MATH-1A-05-W19': {'grading p

In [32]:
secondary_data["Judson-MATH-1A-01-W19"]

{'grading policy | marks distribution': 'Grade\nYour grade will be computed using the following grade distribution.\n5% Labs 10% Quizzes. 8 Ch. 4.4\n\nQuiz 9\nHw 13 due\n22 Lab 6due\n\n \n\x0cLab Grading Policies. will be graded out of 5 points each. You will not know which 4 problems will be graded. For the. Grading Scale\n\nDue to the complexity of the material the grading scale we will use is as follows. General Grading: Each lab member is required to turn in their own lab report. Failure to turn in a. ',
 'attendance policy': 'Accomodations\n\nHonors. Those of you who need additional accommodations, due to disability, campus-related. may, of course, make arrangements with other members of the class to declare yourself as part of. course you are not required to do the Honors Problems. No late work will be accepted. Your. Incompletes: To avoid groups being penalized for a member who does not complete certain sections. '}

In [29]:
with open('../data/secondary_data.json', 'w') as outfile:
    json.dump(secondary_data, outfile, indent=4)

## Generation

In [33]:
import ollama


In [80]:
question="You can only answer in YES or NO. Analyse the following text about a classroom syllabus and respond if student attendance is mandatory or not, in other words do students need to attend all classes or not. If you can't deduce the answer then respond NO. Text : "
retrieved_text = "College Policies:. Honors: An Honors cohort is being offered in this section. If you are in the Honors Program you. an Honors class. The Honors cohort entails additional work and you will earn an Honors. disrupts the class may be asked to leave.. If you are not a member of the Honors Program but think you may be eligible to join, and want to. "
prompt = question + retrieved_text

In [81]:
response = ollama.generate(model='phi3', prompt=prompt)

In [82]:
print(response['response'])

NO

(The text provided does not explicitly state whether student attendance is mandatory or if students need to attend all classes.)


In [49]:
secondary_data = json.load(open('../data/secondary_data.json'))
secondary_data

{'Judson-MATH-1A-01-W19': {'grading policy | marks distribution': 'Grade\nYour grade will be computed using the following grade distribution.\n5% Labs 10% Quizzes. 8 Ch. 4.4\n\nQuiz 9\nHw 13 due\n22 Lab 6due\n\n \n\x0cLab Grading Policies. will be graded out of 5 points each. You will not know which 4 problems will be graded. For the. Grading Scale\n\nDue to the complexity of the material the grading scale we will use is as follows. General Grading: Each lab member is required to turn in their own lab report. Failure to turn in a. ',
  'attendance policy': 'Accomodations\n\nHonors. Those of you who need additional accommodations, due to disability, campus-related. may, of course, make arrangements with other members of the class to declare yourself as part of. course you are not required to do the Honors Problems. No late work will be accepted. Your. Incompletes: To avoid groups being penalized for a member who does not complete certain sections. '},
 'Lien-MATH-1A-05-W19': {'grading p

In [55]:
tag = "attendance policy"

In [83]:
result = {}

In [84]:
def find_first_occurrence(s):
    # Initialize positions with a high value
    pos_yes = s.find("yes")
    pos_no = s.find("no")
    # pos_null = s.find("null")
    
    # Filter out substrings not found (pos will be -1)
    positions = [(pos_yes, "yes"), (pos_no, "no")]
    positions = [pos for pos in positions if pos[0] != -1]
    
    if not positions:
        return "no"
    
    # Return the substring with the smallest position
    return min(positions)[1]

In [85]:
for course in secondary_data:
    print(course)
    if tag in secondary_data[course].keys():
        prompt = question + secondary_data[course][tag]
        response = ollama.generate(model='phi3', prompt=prompt)['response'].lower()
        
        if course not in result:
            result[course] = {}
        result[course][tag] = find_first_occurrence(response)
        # print(response)

    else:
        break

Judson-MATH-1A-01-W19
Lien-MATH-1A-05-W19
Howard-MATH-1A-07-W19
Mailhot-MATH-1A-09-W19
Nay-MATH-1A-11-W19
Mailhot-MATH-1A-23-W19
Lopez-MATH-1A-25-W19
Howard-MATH-1A-27-W19
Du-MATH-1A-63-W19
Dhaliwal-MATH-1A-67Z-W19
Taylor-MATH-1B-01-W19
Taylor-MATH-1B-03-W19
Arabhi-MATH-1B-05-W19
Lo-MATH-1B-07-W19
Delgado-MATH-1B-09-W19
Lo-MATH-1B-11-W19
Parrish-MATH-1B-22-W19
SadeghiHassanvand-MATH-1B-23-W19
Ison-MATH-1B-27-W19
Du-MATH-1B-28-W19
Yu-MATH-1B-63-W19
Ison-MATH-1B-67Z-W19
Nay-MATH-1C-03-W19
Shi-MATH-1C-09-W19
Khosravi-MATH-1C-23-W19
Ison-MATH-1C-27-W19
Guerrero-MATH-1C-61-W19
Nguyen-MATH-1C-63-W19
Bourgoub-MATH-1D-03-W19
Kryliouk-MATH-1D-07-W19
Khosravi-MATH-1D-21-W19
Njinimbam-MATH-1D-27-W19
Mosh-MATH-1D-61-W19
Kryliouk-MATH-2A-03-W19
Khosravi-MATH-2A-11-W19
Mosh-MATH-2A-63-W19
Judson-MATH-2B-03-W19
Mosh-MATH-2B-25-W19
Shukla-MATH-10-01-W19
Bourgoub-MATH-10-02-W19
Nguyen-MATH-10-03-W19
Bensidi-MATH-10-04-W19
Rashid-MATH-10-06-W19
Shukla-MATH-10-07-W19
Desilets-MATH-10-08-W19
Desilets-MATH

In [72]:
secondary_data["Judson-MATH-1A-01-W19"].keys()

dict_keys(['grading policy | marks distribution', 'attendance policy'])

In [87]:
result

{'Judson-MATH-1A-01-W19': {'attendance policy': 'no'},
 'Lien-MATH-1A-05-W19': {'attendance policy': 'yes'},
 'Howard-MATH-1A-07-W19': {'attendance policy': 'no'},
 'Mailhot-MATH-1A-09-W19': {'attendance policy': 'no'},
 'Nay-MATH-1A-11-W19': {'attendance policy': 'yes'},
 'Mailhot-MATH-1A-23-W19': {'attendance policy': 'no'},
 'Lopez-MATH-1A-25-W19': {'attendance policy': 'no'},
 'Howard-MATH-1A-27-W19': {'attendance policy': 'yes'},
 'Du-MATH-1A-63-W19': {'attendance policy': 'yes'},
 'Dhaliwal-MATH-1A-67Z-W19': {'attendance policy': 'yes'},
 'Taylor-MATH-1B-01-W19': {'attendance policy': 'yes'},
 'Taylor-MATH-1B-03-W19': {'attendance policy': 'yes'},
 'Arabhi-MATH-1B-05-W19': {'attendance policy': 'yes'},
 'Lo-MATH-1B-07-W19': {'attendance policy': 'yes'},
 'Delgado-MATH-1B-09-W19': {'attendance policy': 'yes'},
 'Lo-MATH-1B-11-W19': {'attendance policy': 'yes'},
 'Parrish-MATH-1B-22-W19': {'attendance policy': 'yes'},
 'SadeghiHassanvand-MATH-1B-23-W19': {'attendance policy': 'yes'

In [24]:
from langchain_community.llms import Ollama

In [25]:
llm = Ollama(model="phi3")

In [27]:
# llm.invoke("Tell me a joke")

In [11]:
retrieved_data = ""
secondary_data = json.load(open('../data/secondary_data.json'))
print(secondary_data)


{'Judson-MATH-1A-01-W19': {'grading policy | marks distribution': 'Grade\nYour grade will be computed using the following grade distribution.\n5% Labs 10% Quizzes. 8 Ch. 4.4\n\nQuiz 9\nHw 13 due\n22 Lab 6due\n\n \n\x0cLab Grading Policies. will be graded out of 5 points each. You will not know which 4 problems will be graded. For the. Grading Scale\n\nDue to the complexity of the material the grading scale we will use is as follows. General Grading: Each lab member is required to turn in their own lab report. Failure to turn in a. '}, 'Lien-MATH-1A-05-W19': {'grading policy | marks distribution': 'Final grades are non-negotiable. You should monitor your scores in the gradebook regularly. QUESTION: What is my current grade in the class?. Breakdown of grades:\nHomework\n63-879% «BO\n\n80-82.9% «|B\n63-679% «(DS\n60-62.9% «(| D-. marks incorrectly. Problems must be brought to my attention immediately after exams are returned.. - You are required to come to class prepared WITH lecture note

In [58]:
for course in secondary_data:
    print(course)
    retrieved_data += course + " :\n "+ secondary_data[course]["grading policy | marks distribution"] + "\n\n"

Judson-MATH-1A-01-W19
Lien-MATH-1A-05-W19
Howard-MATH-1A-07-W19
Mailhot-MATH-1A-09-W19
Nay-MATH-1A-11-W19
Mailhot-MATH-1A-23-W19
Lopez-MATH-1A-25-W19
Howard-MATH-1A-27-W19
Du-MATH-1A-63-W19
Dhaliwal-MATH-1A-67Z-W19


In [59]:
print(retrieved_data)

Judson-MATH-1A-01-W19 :
 Grade
Your grade will be computed using the following grade distribution.
5% Labs 10% Quizzes. 8 Ch. 4.4

Quiz 9
Hw 13 due
22 Lab 6due

 
Lab Grading Policies. will be graded out of 5 points each. You will not know which 4 problems will be graded. For the. Grading Scale

Due to the complexity of the material the grading scale we will use is as follows. General Grading: Each lab member is required to turn in their own lab report. Failure to turn in a. 

Lien-MATH-1A-05-W19 :
 Final grades are non-negotiable. You should monitor your scores in the gradebook regularly. QUESTION: What is my current grade in the class?. Breakdown of grades:
Homework
63-879% «BO

80-82.9% «|B
63-679% «(DS
60-62.9% «(| D-. marks incorrectly. Problems must be brought to my attention immediately after exams are returned.. - You are required to come to class prepared WITH lecture notes printed out.

GRADING. 

Howard-MATH-1A-07-W19 :
 Grading:. the course, and letter grades will be deter

In [23]:
from langchain_core.output_parsers import StrOutputParser
from langchain_core.prompts import PromptTemplate

In [68]:
prompt = "Analyse the grading policies from the following retrieved docs of various courses. Summarize the information under 1 sentence. Be very concise with your answer and to the point." + retrieved_data

In [69]:
llm.invoke(prompt)

"Judson-MATH-1A-01-W19 grading includes lab work (5%), quizzes (10%), and chapter 4 assignments (8%). Howard-MATH-1A-27-W19 employs a curve set at the instructor's discretion, with potential adjustments after key exams. Lopez-MATH-1A-25-W19 has strict penalties for incorrect answers or changes in grades post assessment submissions. Dhaliwal-MATH-1A-67Z-W19 utilizes a weighted grading system of 15% quizzes, 45% exams (3), and 20% final exam with no grade drops.<|end|><|endoftext|>"

In [ ]:
extracting


attendance polcy: YES / NO / No-Info.....
grading policy: 
tutoring- in person hybrid



table, csv, db

SQL to static



